# 큰 그림 
----
1. midi dataset file을 다루는 util function 정리,
2. torch.utils.dataloader custom class 디자인
3. hirachical lstm (proposed by google) 모델 디자인, 코딩
4. 학습
5. 결과 확인한 후 데이터 더 수집, 

# 만들어야 할 midi dataset - related functions
----
1. single track인지 아닌지 
    - (~= 목표는 monophonic인지 아닌지를 찾는 거지만 일단 지금 단계에서는 보류)
2. single track이라면 피아노인지, 드럼인지, 베이스인지
3. 크롭을 하기 위해 필요한 정보 (fs?)
4. (번외) visualize and listen 한 큐에 하는 함수
5. 크롭 함수 인터페이스 디자인
    - 길이로 할 것 (from, to) or (from, total sec)
    - 비율도 지원할까?
6. piano roll이나 pretty midi class 를 midi로 저장하는 함수
    - piano roll to pm class (v)
    - pm class to midi
    

In [26]:
import pretty_midi

example_file = "./clean_midi/Bach Johann Sebastian/Bach.mid"

In [2]:
pm = pretty_midi.PrettyMIDI(example_file)

In [3]:
pm.get_end_time()

67.333952812500002

In [4]:
pm.get_beats()

array([  0.     ,   0.58823,   1.17646,   1.76469,   2.35292,   2.94115,
         3.52938,   4.11761,   4.70584,   5.29407,   5.8823 ,   6.47053,
         7.05876,   7.64699,   8.23522,   8.82345,   9.41168,   9.99991,
        10.58814,  11.17637,  11.7646 ,  12.35283,  12.94106,  13.52929,
        14.11752,  14.70575,  15.29398,  15.88221,  16.47044,  17.05867,
        17.6469 ,  18.23513,  18.82336,  19.41159,  19.99982,  20.58805,
        21.17628,  21.76451,  22.35274,  22.94097,  23.5292 ,  24.11743,
        24.70566,  25.29389,  25.88212,  26.47035,  27.05858,  27.64681,
        28.23504,  28.82327,  29.4115 ,  29.99973,  30.58796,  31.17619,
        31.76442,  32.35265,  32.94088,  33.52911,  34.11734,  34.70557,
        35.2938 ,  35.88203,  36.47026,  37.05849,  37.64672,  38.23495,
        38.82318,  39.41141,  39.99964,  40.58787,  41.1761 ,  41.76433,
        42.35256,  42.94079,  43.52902,  44.11725,  44.70548,  45.29371,
        45.88194,  46.47017,  47.0584 ,  47.64663, 

In [5]:
pm_roll = pm.get_piano_roll()
pm_roll.shape

(128, 6733)

In [6]:
# import fluidsynth
import IPython.display

In [7]:
IPython.display.Audio(pm.synthesize(fs=16000), rate=16000)

In [8]:
from reverse_pianoroll import *

In [9]:
len(pm_roll[0])

6733

In [10]:
new_pm = piano_roll_to_pretty_midi(pm_roll[:, 2000:5000])

In [38]:
IPython.display.Audio(new_pm.synthesize(fs=16000), rate=16000)

In [48]:
def show_midi(pm, roll=False):
    if not roll and isinstance(pm, pretty_midi.PrettyMIDI):
        IPython.display.display(IPython.display.Audio(pm.synthesize(fs=16000), rate=16000))
    elif roll:
        new_pm = piano_roll_to_pretty_midi(pm)
        IPython.display.display(IPython.display.Audio(new_pm.synthesize(fs=16000), rate=16000))
    else:
        print("show_midi Warning : unexpected arguments")

In [49]:
show_midi(new_pm)

In [12]:
def is_single_track(pm):
    l = len(pm.instruments)
    if l != 1:
        return False
    else:
        return True

In [13]:
is_single_track(pm)

True

In [14]:
pm.instruments[0].is_drum

False

In [15]:
def is_piano_track(pm):
    if is_single_track(pm):
        return not pm.instruments[0].is_drum
    else:
        for inst in pm.instruments:
            if inst.is_drum:
                return False
        return True

In [16]:
inst = pm.instruments[0]
inst

Instrument(program=0, is_drum=False, name="A.PIANO")

In [17]:
len(inst.notes)

710

In [18]:
def save_pm(pm, path):
    pm.write(path)

In [19]:
import glob, os 

In [23]:
midi_list = glob.glob("../midi1/*.mid")

In [27]:
for midi in midi_list:
    print(f"processing {midi}")
    pm_midi = pretty_midi.PrettyMIDI(midi)
    if not is_single_track(pm_midi):
        continue
    if not is_piano_track(pm_midi):
        continue
    print(pm_midi.get_end_time())

processing ../midi1\Bach_BWV849-01_001_20090916-SMD.mid
156.535416667
processing ../midi1\Bach_BWV875-01_002_20090916-SMD.mid
100.289583333
processing ../midi1\Bach_BWV875-02_002_20090916-SMD.mid
117.728125
processing ../midi1\Bach_BWV888-01_008_20110315-SMD.mid
132.740625
processing ../midi1\Bach_BWV888-02_008_20110315-SMD.mid
73.69375
processing ../midi1\Bartok_SZ080-01_002_20110315-SMD.mid
282.883333333
processing ../midi1\Bartok_SZ080-03_002_20110315-SMD.mid
212.286458333
processing ../midi1\Beethoven_Op027No1-03_003_20090916-SMD.mid
336.066666667
processing ../midi1\Beethoven_Op031No2-01_002_20090916-SMD (1).mid
529.615625
processing ../midi1\Beethoven_Op031No2-01_002_20090916-SMD.mid
529.615625
processing ../midi1\Beethoven_Op031No2-02_002_20090916-SMD (1).mid
507.3625
processing ../midi1\Beethoven_Op031No2-02_002_20090916-SMD.mid
507.3625
processing ../midi1\Beethoven_Op031No2-03_002_20090916-SMD.mid
400.266666667
processing ../midi1\Beethoven_WoO080_001_20081107-SMD.mid
658.313